In [ ]:
!pip install pycaret[full]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 320 kB 5.2 MB/s 
     |████████████████████████████████| 3.3 MB 43.0 MB/s 
     |████████████████████████████████| 137 kB 50.4 MB/s 
     |████████████████████████████████| 88 kB 5.8 MB/s 
     |████████████████████████████████| 167 kB 43.9 MB/s 
     |████████████████████████████████| 1.7 MB 49.4 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 4.8 MB 38.1 MB/s 
     |████████████████████████████████| 2.0 MB 48.4 MB/s 
     |████████████████████████████████| 56 kB 4.4 MB/s 
     |████████████████████████████████| 6.8 MB 53.0 MB/s 
     |████████████████████████████████| 25.9 MB 1.7 MB/s 
     |████████████████████████████████| 636 kB 47.3 MB/s 
     |████████████████████████████████| 1

In [ ]:
!pip install surprise

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 11.8 MB 5.0 MB/s 
  Created wheel for scikit-surprise: filename=scikit_surprise-1.1.1-cp37-cp37m-linux_x86_64.whl size=1627538 sha256=16939b8891a63e850c8dfbc1f6ab0682bf9b112b5cb80423aec8f5a61edfb203
  Stored in directory: /root/.cache/pip/wheels/76/44/74/b498c42be47b2406bd27994e16c5188e337c657025ab400c1c
Successfully built scikit-surprise


In [ ]:
from google.colab import drive 
from pycaret.utils import enable_colab
enable_colab()
drive.mount('/content/drive')

Colab mode enabled.
Mounted at /content/drive


In [ ]:
import numpy as np
import pandas as pd

from pycaret.classification import *

In [ ]:
info_df_TRAIN = pd.read_csv("/content/drive/MyDrive/DSML/Traveldata_Train.csv")
response_df_TRAIN = pd.read_csv("/content/drive/MyDrive/DSML/Surveydata_Train.csv")

info_df_TEST = pd.read_csv("/content/drive/MyDrive/DSML/Traveldata_Test.csv")
response_df_TEST = pd.read_csv("/content/drive/MyDrive/DSML/Surveydata_Test.csv")

In [ ]:
df_TRAIN = info_df_TRAIN.merge(response_df_TRAIN, how='inner', on='ID')
df_TEST = info_df_TEST.merge(response_df_TEST, how='inner', on='ID')
print(df_TRAIN.shape)
print(df_TEST.shape)

(94379, 25)
(35602, 24)


In [ ]:
!cp "/content/drive/MyDrive/DSML/categorical_imputation.py" "/content"
!cp "/content/drive/MyDrive/DSML/numeric_imputation.py" "/content"

In [ ]:
from numeric_imputation import replace_with_regression
from categorical_imputation import *

In [ ]:
df_TRAIN_regression = replace_with_regression(df=df_TRAIN, existed_variables=['Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins'])
df_TEST_regression = replace_with_regression(df=df_TEST, existed_variables=['Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins'])

score: 0.932157468408056
coef: [[0.9771727]]
score: 0.9309256405582267
coef: [[0.98315735]]


In [ ]:
params = {
    'cid_col': ['ID'],
    'iid_col': [
        'Seat_Comfort', 'Arrival_Time_Convenient', 'Catering', 'Platform_Location', 'Onboard_Wifi_Service',
        'Onboard_Entertainment', 'Online_Support', 'Ease_of_Online_Booking', 'Onboard_Service', 'Legroom',
        'Baggage_Handling', 'CheckIn_Service', 'Cleanliness', 'Online_Boarding'
    ],
    'iid_colname': 'Question',
    'cid_colname': 'ID',
    'response_colname': 'Response',
    'response_map': {
        'Extremely Poor': 0,
        'Very Inconvenient': 0,
        'Poor': 1,
        'Inconvenient': 1,
        'Needs Improvement': 2,
        'Manageable': 3, 
        'Acceptable': 3,
        'Good': 4,
        'Convenient': 4, 
        'Excellent': 5,
        'Very Convenient': 5
    },
    'response_scale': (0, 5),
    'model_params': {
        'lr_all': 0.001, 
        'n_epochs': 100, 
        'n_factors': 300
    }
}

In [ ]:
interaction_df_melted, le, model = create_mf_model(df=df_TRAIN_regression, **params)
interaction_matrix_fn = make_response_prediction(df=interaction_df_melted, le=le, model=model, cid_colname='ID', iid_colname='Question', response_colname='Response')
df_TRAIN_preprocessed = finalize_matrix_completion(df=df_TRAIN_regression, interaction_df=interaction_matrix_fn, non_iid_cols=['Gender', 'Customer_Type', 'Age', 'Type_Travel', 'Travel_Class', 'Travel_Distance', 'Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins', 'Overall_Experience', 'Seat_Class'])

RMSE: 1.0204


In [ ]:
interaction_df_melted, le, model = create_mf_model(df=df_TEST_regression, **params)
interaction_matrix_fn = make_response_prediction(df=interaction_df_melted, le=le, model=model, cid_colname='ID', iid_colname='Question', response_colname='Response')
df_TEST_preprocessed = finalize_matrix_completion(df=df_TEST_regression, interaction_df=interaction_matrix_fn, non_iid_cols=['Gender', 'Customer_Type', 'Age', 'Type_Travel', 'Travel_Class', 'Travel_Distance', 'Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins', 'Seat_Class'])

RMSE: 1.0233


In [ ]:
preprocess_pipeline = {
    
    # IMPUTATION
    'imputation_type': 'iterative',    
    
    # ENCODING
    
    # OUTLIERS
    'remove_outliers': True,
    
    # SCALE
    'normalize': True,
    
    # FE 
    'feature_interaction': True,
    'group_features': [
        ['Seat_Comfort', 'Catering', 'Platform_Location', 'Arrival_Time_Convenient'], 
        ['Onboard_Wifi_Service', 'Onboard_Entertainment', 'Ease_of_Online_Booking', 'Online_Boarding', 'Online_Support'],
        ['Ease_of_Online_Booking', 'Baggage_Handling', 'Onboard_Service', 'Cleanliness', 'Legroom']
    ],
    
    # FS 
    'feature_selection': True, 
    'remove_multicollinearity': True
    
}

In [ ]:
clf_exp_fn = setup(
    data=df_TRAIN_preprocessed, target="Overall_Experience", 
    session_id=12345, fold=5,
    **preprocess_pipeline
)

Description                            Value
0                               session_id                            12345
1                                   Target               Overall_Experience
2                              Target Type                           Binary
3                            Label Encoded                             None
4                            Original Data                      (94379, 25)
5                           Missing Values                             True
6                         Numeric Features                               19
7                     Categorical Features                                5
8                         Ordinal Features                            False
9                High Cardinality Features                            False
10                 High Cardinality Method                             None
11                   Transformed Train Set                      (62761, 58)
12                    Transformed Test Set                      (28314, 58)
13                      Shuffle Train-Test                             True
14                     Stratify Train-Test                            False
15                          Fold Generator                  StratifiedKFold
16                             Fold Number                                5
17                                CPU Jobs                               -1
18                                 Use GPU                            False
19                          Log Experiment                            False
20                         Experiment Name                 clf-default-name
21                                     USI                             814b
22                         Imputation Type                        iterative
23          Iterative Imputation Iteration                                5
24                         Numeric Imputer                             mean
25      Iterative Imputation Numeric Model  Light Gradient Boosting Machine
26                     Categorical Imputer                         constant
27  Iterative Imputation Categorical Model  Light Gradient Boosting Machine
28           Unknown Categoricals Handling                   least_frequent
29                               Normalize                             True
30                        Normalize Method                           zscore
31                          Transformation                            False
32                   Transformation Method                             None
33                                     PCA                            False
34                              PCA Method                             None
35                          PCA Components                             None
36                     Ignore Low Variance                            False
37                     Combine Rare Levels                            False
38                    Rare Level Threshold                             None
39                         Numeric Binning                            False
40                         Remove Outliers                             True
41                      Outliers Threshold                             0.05
42                Remove Multicollinearity                             True
43             Multicollinearity Threshold                              0.9
44             Remove Perfect Collinearity                             True
45                              Clustering                            False
46                    Clustering Iteration                             None
47                     Polynomial Features                            False
48                       Polynomial Degree                             None
49                    Trignometry Features                            False
50                    Polynomial Threshold                             None
51                          Group Features                             True
52 

INFO:logs:create_model_container: 0
INFO:logs:master_model_container: 0
INFO:logs:display_container: 1
INFO:logs:Pipeline(memory=None,
         steps=[('dtypes',
                 DataTypes_Auto_infer(categorical_features=[],
                                      display_types=True, features_todrop=[],
                                      id_columns=['ID'],
                                      ml_usecase='classification',
                                      numerical_features=[],
                                      target='Overall_Experience',
                                      time_features=[])),
                ('imputer',
                 Iterative_Imputer(add_indicator=False,
                                   classifier=LGBMClassifier(boosting_type='gbdt',
                                                             class_weight=None,...
                 Fix_multicollinearity(correlation_with_target_preference=None,
                                       correlation_with_t

In [ ]:
X = get_config('X')
pipeline = get_config('prep_pipe')

INFO:logs:Initializing get_config()
INFO:logs:get_config(variable=X)
INFO:logs:Global variable: X returned as        Type_Travel_Business Travel  Online_Support  Gender_Female  \
0                              1.0       -0.393490            1.0   
1                              0.0        0.368188            0.0   
2                              1.0        1.129866            1.0   
3                              1.0       -0.393490            1.0   
4                              1.0        1.129866            1.0   
...                            ...             ...            ...   
94374                          1.0       -1.916847            0.0   
94375                          1.0        1.129866            0.0   
94376                          1.0        0.368188            0.0   
94377                          0.0        0.368188            0.0   
94378                          0.0       -0.393490            0.0   

       group_0_Std  Onboard_Entertainment  group_2_Std  Check

In [ ]:
models = compare_models(n_select=5)

Model  Accuracy     AUC  Recall   Prec.  \
catboost              CatBoost Classifier    0.9557  0.9933  0.9534  0.9665   
xgboost         Extreme Gradient Boosting    0.9532  0.9927  0.9499  0.9654   
rf               Random Forest Classifier    0.9528  0.9916  0.9494  0.9652   
lightgbm  Light Gradient Boosting Machine    0.9524  0.9925  0.9481  0.9657   
et                 Extra Trees Classifier    0.9515  0.9912  0.9491  0.9633   
knn                K Neighbors Classifier    0.9339  0.9769  0.9243  0.9555   
gbc          Gradient Boosting Classifier    0.9328  0.9845  0.9345  0.9441   
dt               Decision Tree Classifier    0.9226  0.9216  0.9306  0.9304   
ada                  Ada Boost Classifier    0.9160  0.9774  0.9187  0.9296   
lr                    Logistic Regression    0.8979  0.9619  0.9089  0.9078   
svm                   SVM - Linear Kernel    0.8966  0.0000  0.9011  0.9122   
ridge                    Ridge Classifier    0.8917  0.0000  0.9026  0.9029   
lda          Linear Discriminant Analysis    0.8917  0.9590  0.9025  0.9030   
nb                            Naive Bayes    0.8752  0.9445  0.8644  0.9071   
qda       Quadratic Discriminant Analysis    0.6795  0.6868  0.6221  0.7555   
dummy                    Dummy Classifier    0.5567  0.5000  1.0000  0.5567   

              F1   Kappa     MCC  TT (Sec)  
catboost  0.9599  0.9104  0.9105    31.684  
xgboost   0.9576  0.9053  0.9055    14.442  
rf        0.9572  0.9045  0.9047     9.170  
lightgbm  0.9568  0.9037  0.9039     2.342  
et        0.9561  0.9019  0.9020     7.440  
knn       0.9396  0.8666  0.8672   107.602  
gbc       0.9393  0.8639  0.8640    20.496  
dt        0.9305  0.8432  0.8432     1.028  
ada       0.9241  0.8301  0.8302     4.476  
lr        0.9083  0.7930  0.7930     2.900  
svm       0.9065  0.7907  0.7909     0.620  
ridge     0.9027  0.7806  0.7806     0.132  
lda       0.9027  0.7807  0.7807     0.722  
nb        0.8852  0.7487  0.7497     0.142  
qda       0.6764  0.3672  0.3763     0.360  
dummy     0.7152  0.0000  0.0000     0.092

INFO:logs:create_model_container: 16
INFO:logs:master_model_container: 16
INFO:logs:display_container: 2
INFO:logs:[<catboost.core.CatBoostClassifier object at 0x7ff6790fa590>, XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, objective='binary:logistic',
              predictor='auto', random_state=12345, reg_alpha=0, ...), RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criteri

In [ ]:
models_score_grid = pull()
models_mean, models_std = models_score_grid['Accuracy'].mean(), models_score_grid['Accuracy'].std()
print([models_mean - models_std, models_mean, models_mean + models_std])

[0.7752368750492244, 0.8850125, 0.9947881249507755]


## **SINGLE MODEL**

**BASELINE**

In [ ]:
choose_model = models[0]

In [ ]:
predict_model(choose_model);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7ff6790fa590>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier     0.958  0.9939  0.9549  0.9678  0.9613  0.9155   

      MCC  
0  0.9156

**OPTIMIZED**

**Search Algorithm: Scikit-Learn > RandomGridSearch**

In [ ]:
choose_model_optimized_1 = tune_model(estimator=choose_model, fold=3, n_iter=30, choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9538  0.9928  0.9499  0.9665  0.9582  0.9067  0.9068
1       0.9557  0.9932  0.9562  0.9640  0.9601  0.9104  0.9104
2       0.9540  0.9925  0.9519  0.9649  0.9584  0.9069  0.9070
Mean    0.9545  0.9928  0.9527  0.9652  0.9589  0.9080  0.9081
Std     0.0009  0.0003  0.0026  0.0011  0.0009  0.0017  0.0017

INFO:logs:create_model_container: 18
INFO:logs:master_model_container: 18
INFO:logs:display_container: 4
INFO:logs:<catboost.core.CatBoostClassifier object at 0x7ff6786306d0>
INFO:logs:tune_model() succesfully completed......................................


In [ ]:
predict_model(choose_model_optimized_1);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7ff6786306d0>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier     0.958  0.9939  0.9549  0.9678  0.9613  0.9155   

      MCC  
0  0.9156

**Search Algorithm: Scikit-Optimize > BayesSearch**

In [ ]:
choose_model_optimized_2 = tune_model(estimator=choose_model, fold=3, n_iter=30, search_library='scikit-optimize', search_algorithm='bayesian', choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9535  0.9924  0.9491  0.9669  0.9579  0.9061  0.9063
1       0.9556  0.9927  0.9547  0.9653  0.9599  0.9103  0.9103
2       0.9535  0.9922  0.9523  0.9638  0.9580  0.9060  0.9061
Mean    0.9542  0.9925  0.9520  0.9653  0.9586  0.9074  0.9076
Std     0.0010  0.0002  0.0023  0.0013  0.0009  0.0020  0.0020

INFO:logs:create_model_container: 20
INFO:logs:master_model_container: 20
INFO:logs:display_container: 6
INFO:logs:<catboost.core.CatBoostClassifier object at 0x7ff67982b790>
INFO:logs:tune_model() succesfully completed......................................


In [ ]:
predict_model(choose_model_optimized_2);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7ff67982b790>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier     0.958  0.9939  0.9549  0.9678  0.9613  0.9155   

      MCC  
0  0.9156

## **MULTIPLE MODELS**

In [ ]:
estimators = [tune_model(estimator=model, fold=3, n_iter=30, search_library='scikit-optimize', search_algorithm='bayesian', choose_better=True) for model in models[:3]]

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9446  0.9885  0.9238  0.9753  0.9488  0.8884  0.8900
1       0.9457  0.9893  0.9281  0.9731  0.9501  0.8906  0.8918
2       0.9455  0.9886  0.9292  0.9717  0.9500  0.8902  0.8913
Mean    0.9453  0.9888  0.9270  0.9734  0.9496  0.8898  0.8910
Std     0.0005  0.0004  0.0023  0.0015  0.0006  0.0010  0.0008

INFO:logs:create_model_container: 26
INFO:logs:master_model_container: 26
INFO:logs:display_container: 10
INFO:logs:RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='auto',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=-1, oob_score=False, random_state=12345,
                       verbose=0, warm_start=False)
INFO:logs:tune_model() succesfully completed......................................


**BLEND - BASELINE**

In [ ]:
blender = blend_models(estimator_list=models[:3], fold=3, choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9546  0.9929  0.9503  0.9676  0.9588  0.9082  0.9084
1       0.9565  0.9933  0.9543  0.9672  0.9607  0.9121  0.9122
2       0.9546  0.9928  0.9515  0.9665  0.9589  0.9083  0.9084
Mean    0.9553  0.9930  0.9520  0.9671  0.9595  0.9095  0.9097
Std     0.0009  0.0002  0.0017  0.0004  0.0009  0.0018  0.0018

INFO:logs:create_model_container: 30
INFO:logs:master_model_container: 30
INFO:logs:display_container: 11
INFO:logs:<catboost.core.CatBoostClassifier object at 0x7ff675c6f510>
INFO:logs:blend_models() succesfully completed......................................


In [ ]:
predict_model(blender);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7ff675c6f510>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier     0.958  0.9939  0.9549  0.9678  0.9613  0.9155   

      MCC  
0  0.9156

**BLEND - OPTIMIZED**

In [ ]:
blender_optimized = blend_models(estimator_list=estimators, fold=3, choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9554  0.9929  0.9503  0.9689  0.9595  0.9098  0.9100
1       0.9567  0.9932  0.9553  0.9666  0.9609  0.9124  0.9125
2       0.9551  0.9927  0.9527  0.9661  0.9594  0.9091  0.9092
Mean    0.9557  0.9929  0.9527  0.9672  0.9599  0.9104  0.9106
Std     0.0007  0.0002  0.0020  0.0012  0.0007  0.0014  0.0014

INFO:logs:create_model_container: 34
INFO:logs:master_model_container: 34
INFO:logs:display_container: 13
INFO:logs:VotingClassifier(estimators=[('catboost',
                              <catboost.core.CatBoostClassifier object at 0x7ff676c7b250>),
                             ('xgboost',
                              XGBClassifier(base_score=0.5, booster='gbtree',
                                            callbacks=None, colsample_bylevel=1,
                                            colsample_bynode=1,
                                            colsample_bytree=0.7722483424852585,
                                            early_stopping_rounds=None,
                                            enable_categorical=False,
                                            eval_metric=None, gamma=0,
                                            gpu_id=-1, grow_policy='dept...
                                                     max_depth=None,
                                               

In [ ]:
predict_model(blender_optimized);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=VotingClassifier(estimators=[('catboost',
                              <catboost.core.CatBoostClassifier object at 0x7ff676c7b250>),
                             ('xgboost',
                              XGBClassifier(base_score=0.5, booster='gbtree',
                                            callbacks=None, colsample_bylevel=1,
                                            colsample_bynode=1,
                                            colsample_bytree=0.7722483424852585,
                                            early_stopping_rounds=None,
                                            enable_categorical=False,
                                            eval_metric=None, gamma=0,
                                            gpu_id=-1, grow_policy='dept...
                                                     max_depth=None,
                                                     max_features='auto',
                

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
0  Voting Classifier    0.9582  0.9935  0.9542  0.9687  0.9614  0.9158  0.9159

**STACK - BASELINE**

In [ ]:
stacker_1 = stack_models(estimator_list=models[:3], fold=3, meta_model_fold=3, restack=False, choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9542  0.9929  0.9539  0.9635  0.9587  0.9073  0.9074
1       0.9569  0.9932  0.9582  0.9641  0.9612  0.9127  0.9127
2       0.9542  0.9927  0.9547  0.9628  0.9587  0.9073  0.9074
Mean    0.9551  0.9929  0.9556  0.9635  0.9595  0.9091  0.9092
Std     0.0013  0.0002  0.0019  0.0006  0.0012  0.0025  0.0025

INFO:logs:create_model_container: 38
INFO:logs:master_model_container: 38
INFO:logs:display_container: 15
INFO:logs:<catboost.core.CatBoostClassifier object at 0x7ff679aa2710>
INFO:logs:stack_models() succesfully completed......................................


In [ ]:
stacker_2 = stack_models(estimator_list=models[:3], fold=3, meta_model_fold=3, restack=True, choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9545  0.9926  0.9533  0.9646  0.9589  0.9080  0.9081
1       0.9558  0.9927  0.9573  0.9631  0.9602  0.9106  0.9106
2       0.9537  0.9919  0.9535  0.9630  0.9582  0.9064  0.9064
Mean    0.9547  0.9924  0.9547  0.9636  0.9591  0.9083  0.9084
Std     0.0009  0.0003  0.0018  0.0008  0.0008  0.0017  0.0017

INFO:logs:create_model_container: 42
INFO:logs:master_model_container: 42
INFO:logs:display_container: 16
INFO:logs:<catboost.core.CatBoostClassifier object at 0x7ff676bb8e90>
INFO:logs:stack_models() succesfully completed......................................


In [ ]:
meta_model = create_model('lightgbm')
stacker_3 = stack_models(estimator_list=models[:3], fold=3, meta_model_fold=3, restack=True, meta_model=meta_model, choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9573  0.9936  0.9503  0.9723  0.9612  0.9137  0.9140
1       0.9576  0.9937  0.9531  0.9701  0.9615  0.9142  0.9144
2       0.9566  0.9933  0.9481  0.9733  0.9605  0.9124  0.9127
Mean    0.9571  0.9935  0.9505  0.9719  0.9611  0.9134  0.9137
Std     0.0004  0.0002  0.0021  0.0013  0.0004  0.0008  0.0007

INFO:logs:create_model_container: 47
INFO:logs:master_model_container: 47
INFO:logs:display_container: 18
INFO:logs:StackingClassifier(cv=3,
                   estimators=[('catboost',
                                <catboost.core.CatBoostClassifier object at 0x7ff67721e590>),
                               ('xgboost',
                                XGBClassifier(base_score=0.5, booster='gbtree',
                                              callbacks=None,
                                              colsample_bylevel=1,
                                              colsample_bynode=1,
                                              colsample_bytree=1,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None, gamma=0,
                                              gpu_id=-1,
                                              grow_policy='de

In [ ]:
predict_model(stacker_1);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7ff679aa2710>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier     0.958  0.9939  0.9549  0.9678  0.9613  0.9155   

      MCC  
0  0.9156

In [ ]:
predict_model(stacker_2);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7ff676bb8e90>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier     0.958  0.9939  0.9549  0.9678  0.9613  0.9155   

      MCC  
0  0.9156

In [ ]:
predict_model(stacker_3);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=StackingClassifier(cv=3,
                   estimators=[('catboost',
                                <catboost.core.CatBoostClassifier object at 0x7ff67721e590>),
                               ('xgboost',
                                XGBClassifier(base_score=0.5, booster='gbtree',
                                              callbacks=None,
                                              colsample_bylevel=1,
                                              colsample_bynode=1,
                                              colsample_bytree=1,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None, gamma=0,
                                              gpu_id=-1,
                                              grow_policy='depthwise',
                                 

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  Stacking Classifier    0.9609  0.9942  0.9539  0.9739  0.9638  0.9212   

      MCC  
0  0.9215

**STACK - OPTIMIZED**

In [ ]:
meta_model = create_model('lightgbm')
stacker_optimized = stack_models(estimator_list=estimators, fold=3, meta_model_fold=3, restack=True, meta_model=meta_model, choose_better=True)

Accuracy     AUC  Recall   Prec.      F1   Kappa     MCC
Fold                                                          
0       0.9575  0.9936  0.9494  0.9735  0.9613  0.9141  0.9144
1       0.9570  0.9936  0.9517  0.9706  0.9610  0.9132  0.9134
2       0.9564  0.9932  0.9493  0.9716  0.9603  0.9118  0.9121
Mean    0.9569  0.9934  0.9501  0.9719  0.9609  0.9130  0.9133
Std     0.0005  0.0002  0.0011  0.0012  0.0004  0.0009  0.0009

INFO:logs:create_model_container: 52
INFO:logs:master_model_container: 52
INFO:logs:display_container: 23
INFO:logs:StackingClassifier(cv=3,
                   estimators=[('catboost',
                                <catboost.core.CatBoostClassifier object at 0x7ff6765a64d0>),
                               ('xgboost',
                                XGBClassifier(base_score=0.5, booster='gbtree',
                                              callbacks=None,
                                              colsample_bylevel=1,
                                              colsample_bynode=1,
                                              colsample_bytree=0.7722483424852585,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None, gamma=0,
                                              gpu_id=-1,
                                            

In [ ]:
predict_model(stacker_optimized);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=StackingClassifier(cv=3,
                   estimators=[('catboost',
                                <catboost.core.CatBoostClassifier object at 0x7ff6765a64d0>),
                               ('xgboost',
                                XGBClassifier(base_score=0.5, booster='gbtree',
                                              callbacks=None,
                                              colsample_bylevel=1,
                                              colsample_bynode=1,
                                              colsample_bytree=0.7722483424852585,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None, gamma=0,
                                              gpu_id=-1,
                                              grow_polic...
                           

Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  Stacking Classifier    0.9602  0.9941  0.9526  0.9739  0.9631  0.9198   

      MCC  
0  0.9201

## **FINALIZE**

In [ ]:
chosen_model = automl(use_holdout=True)

INFO:logs:Initializing automl()
INFO:logs:automl(optimize=Accuracy, use_holdout=True, return_train_score=False)
INFO:logs:Model Selection Basis : Holdout set
INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=1000,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=12345, solver='lbfgs', tol=0.0001, verbose=0,
                   warm_start=False), probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=False, ml_usecase=None, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
                   intercept_scaling=1, l1_ratio=None, max_iter=1000,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=12345, solver='lbfgs', tol=0.0001, verbose=0,
    

In [ ]:
chosen_model_fn = finalize_model(chosen_model)

INFO:logs:Initializing finalize_model()
INFO:logs:finalize_model(estimator=StackingClassifier(cv=3,
                   estimators=[('catboost',
                                <catboost.core.CatBoostClassifier object at 0x7ff675cf5850>),
                               ('xgboost',
                                XGBClassifier(base_score=0.5, booster='gbtree',
                                              callbacks=None,
                                              colsample_bylevel=1,
                                              colsample_bynode=1,
                                              colsample_bytree=1,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None, gamma=0,
                                              gpu_id=-1,
                                              grow_policy='depthwise',
                               

In [ ]:
pred = predict_model(chosen_model_fn, data=df_TEST_preprocessed)

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=StackingClassifier(cv=3,
                   estimators=[('catboost',
                                <catboost.core.CatBoostClassifier object at 0x7ff679037cd0>),
                               ('xgboost',
                                XGBClassifier(base_score=0.5, booster='gbtree',
                                              callbacks=None,
                                              colsample_bylevel=1,
                                              colsample_bynode=1,
                                              colsample_bytree=1,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None, gamma=0,
                                              gpu_id=-1,
                                              grow_policy='depthwise',
                                 